In [1]:
import time
start=time.time()

# Parsing Reuters 21578

In [2]:
import html
import pprint
import re
from html.parser import HTMLParser

from sklearn.cross_validation import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import confusion_matrix
import warnings
warnings.filterwarnings("ignore")

class ReutersParser(HTMLParser):
    """
    ReutersParser subclasses HTMLParser and is used to open the SGML
    files associated with the Reuters-21578 categorised test collection.

    The parser is a generator and will yield a single document at a time.
    Since the data will be chunked on parsing, it is necessary to keep 
    some internal state of when tags have been "entered" and "exited".
    Hence the in_body, in_topics and in_topic_d boolean members.
    """
    def __init__(self, encoding='latin-1'):
        """
        Initialise the superclass (HTMLParser) and reset the parser.
        Sets the encoding of the SGML files by default to latin-1.
        """
        html.parser.HTMLParser.__init__(self)
        self._reset()
        self.encoding = encoding

    def _reset(self):
        """
        This is called only on initialisation of the parser class
        and when a new topic-body tuple has been generated. It
        resets all off the state so that a new tuple can be subsequently
        generated.
        """
        self.in_body = False
        self.in_topics = False
        self.in_topic_d = False
        self.body = ""
        self.topics = []
        self.topic_d = ""

    def parse(self, fd):
        """
        parse accepts a file descriptor and loads the data in chunks
        in order to minimise memory usage. It then yields new documents
        as they are parsed.
        """
        self.docs = []
        for chunk in fd:
            self.feed(chunk.decode(self.encoding))
            for doc in self.docs:
                yield doc
            self.docs = []
        self.close()

    def handle_starttag(self, tag, attrs):
        """
        This method is used to determine what to do when the parser
        comes across a particular tag of type "tag". In this instance
        we simply set the internal state booleans to True if that particular
        tag has been found.
        """
        if tag == "reuters":
            pass
        elif tag == "body":
            self.in_body = True
        elif tag == "topics":
            self.in_topics = True
        elif tag == "d":
            self.in_topic_d = True 

    def handle_endtag(self, tag):
        """
        This method is used to determine what to do when the parser
        finishes with a particular tag of type "tag". 

        If the tag is a  tag, then we remove all 
        white-space with a regular expression and then append the 
        topic-body tuple.

        If the tag is a  or  tag then we simply set
        the internal state to False for these booleans, respectively.

        If the tag is a  tag (found within a  tag), then we
        append the particular topic to the "topics" list and 
        finally reset it.
        """
        if tag == "reuters":
            self.body = re.sub(r'\s+', r' ', self.body)
            self.docs.append( (self.topics, self.body) )
            self._reset()
        elif tag == "body":
            self.in_body = False
        elif tag == "topics":
            self.in_topics = False
        elif tag == "d":
            self.in_topic_d = False
            self.topics.append(self.topic_d)
            self.topic_d = ""  

    def handle_data(self, data):
        """
        The data is simply appended to the appropriate member state
        for that particular tag, up until the end closing tag appears.
        """
        if self.in_body:
            self.body += data
        elif self.in_topic_d:
            self.topic_d += data


/home/anirban/anaconda3/lib/python3.6/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


# Extracting the topics from Reuters 21578

In [3]:
def obtain_topic_tags():
    """
    Open the topic list file and import all of the topic names
    taking care to strip the trailing "\n" from each word.
    """
    topics = open(
        "all-topics-strings.lc.txt", "r"
    ).readlines()
    topics = [t.strip() for t in topics]
    return topics

# Filtering docs by topics

In [4]:
def filter_doc_list_through_topics(topics, docs):
    """
    Reads all of the documents and creates a new list of two-tuples
    that contain a single feature entry and the body text, instead of
    a list of topics. It removes all geographic features and only 
    retains those documents which have at least one non-geographic
    topic.
    """
    ref_docs = []
    for d in docs:
        if d[0] == [] or d[0] == "":
            continue
        for t in d[0]:
            if t in topics:
                d_tup = (t, d[1])
                ref_docs.append(d_tup)
                break
    return ref_docs

In [5]:
from nltk import word_tokenize
from nltk.stem.porter import PorterStemmer
from nltk.corpus import stopwords
 
cachedStopWords = stopwords.words("english")
 
def tokenize(text):
    min_length = 3
    words = map(lambda word: word.lower(), word_tokenize(text));
    words = [word for word in words
                  if word not in cachedStopWords]
    tokens =(list(map(lambda token: PorterStemmer().stem(token),
                  words)));
    p = re.compile('[a-zA-Z]+');
    filtered_tokens =list(filter(lambda token:
                  p.match(token) and len(token)>=min_length,
         tokens));
    return filtered_tokens

In [6]:
def create_corpus_and_topics(docs):
    # Create the topics bag
    topics = [d[0] for d in docs]
    
    # Create the document corpus list
    corpus = [d[1] for d in docs]
    return corpus,topics

In [7]:
if __name__ == "__main__":
    # Create the list of Reuters data and create the parser
    files = ["reut2-%03d.sgm" % r for r in range(0, 22)]
    parser = ReutersParser()

    # Parse the document and force all generated docs into
    # a list so that it can be printed out to the console
    docs = []
    for fn in files:
        for d in parser.parse(open(fn, 'rb')):
            docs.append(d)
            
            
    # Obtain the topic tags and filter docs through it 
    topics = obtain_topic_tags()
    ref_docs = filter_doc_list_through_topics(topics, docs)
    print(ref_docs)

[('cocoa', 'Showers continued throughout the week in the Bahia cocoa zone, alleviating the drought since early January and improving prospects for the coming temporao, although normal humidity levels have not been restored, Comissaria Smith said in its weekly review. The dry period means the temporao will be late this year. Arrivals for the week ended February 22 were 155,221 bags of 60 kilos making a cumulative total for the season of 5.93 mln against 5.81 at the same stage last year. Again it seems that cocoa delivered earlier on consignment was included in the arrivals figures. Comissaria Smith said there is still some doubt as to how much old crop cocoa is still available as harvesting has practically come to an end. With total Bahia crop estimates around 6.4 mln bags and sales standing at almost 6.2 mln there are a few hundred thousand bags still in the hands of farmers, middlemen, exporters and processors. There are doubts as to how much of this cocoa would be fit for export as s

In [8]:
# Vectorise and TF-IDF transform the corpus 
corpus, topics = create_corpus_and_topics(ref_docs)

In [9]:
end=time.time()
print("Time taken: ",end-start, "seconds")

Time taken:  34.232715368270874 seconds


# Implementing with  test_size = 0.2 that is 20% of the corpus is taken as test

In [10]:
# Create the training-test split of the data
corpus_train,corpus_test,topics_train,topics_test = train_test_split(
        corpus, topics, test_size=0.2, random_state=42
    )

In [11]:
len(corpus_train)

9093

In [12]:
len(corpus_test)

2274

In [13]:
len(topics_train)

9093

In [14]:
len(topics_test)

2274

In [15]:
from sklearn.model_selection import cross_val_score
from sklearn.pipeline import Pipeline    
from sklearn.naive_bayes import MultinomialNB
from sklearn.multiclass import OneVsRestClassifier
pipeline_bayes = Pipeline([
                ('tfidf', TfidfVectorizer(tokenizer=tokenize, min_df=3,
                        max_df=0.90, max_features=3000,
                        use_idf=True, sublinear_tf=True,
                        norm='l2')),
                ('clf',OneVsRestClassifier(MultinomialNB(
                    fit_prior=True, class_prior=None))),
            ])
pipeline_bayes.fit(corpus_train,topics_train)

Pipeline(memory=None,
     steps=[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.9, max_features=3000, min_df=3,
        ngram_range=(1, 1), norm='l2', preprocessor=None, smooth_idf=True,
 ...assifier(estimator=MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True),
          n_jobs=1))])

In [16]:
cv_score_naive_bayes = cross_val_score(pipeline_bayes, corpus_train, topics_train, cv=5)
print("The cross validation score for Naive Bayes is:")
print(cv_score_naive_bayes)

The cross validation score for Naive Bayes is:
[0.70635776 0.7022319  0.70507166 0.71802002 0.72706935]


In [17]:
predicted_topics= pipeline_bayes.predict(corpus_test)

from sklearn.metrics import precision_recall_fscore_support, accuracy_score

accuracy = accuracy_score(topics_test, predicted_topics)
precision, recall, f1_score, _ = precision_recall_fscore_support(topics_test, predicted_topics, average='weighted')# Weighted means the weighted average of the metric scores are given as output

print("Accuracy: ", accuracy)
print("Precision: ", precision)
print("Recall: ", recall)
print("F1 score: ", f1_score)

Accuracy:  0.7484608619173263
Precision:  0.7054023383976247
Recall:  0.7484608619173263
F1 score:  0.6969756712370362


In [18]:
import sklearn
sklearn.metrics.confusion_matrix(topics_test,predicted_topics, labels=None, sample_weight=None)

array([[423,   0,   0, ...,   0,   0,   0],
       [  8,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0],
       ...,
       [  0,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0]])

In [19]:
temp_test={}
temp_predicted={}
for i in range(0,len(corpus_test)):
    if corpus_test[i] in temp_test.keys():
        temp_test[corpus_test[i]].append(topics_test[i])
        temp_predicted[corpus_test[i]].append(predicted_topics[i])
    else:
        temp_test[corpus_test[i]]=[]
        temp_test[corpus_test[i]].append(topics_test[i])
        temp_predicted[corpus_test[i]]=[]
        temp_predicted[corpus_test[i]].append(predicted_topics[i])

for i in temp_test.keys():# To keep only the distinct labels
    temp_test[i]=list(set(temp_test[i]))
    temp_predicted[i]=list(set(temp_predicted[i]))

import pandas as pd
pd.DataFrame(
    {'Test docs': list(temp_test.keys()),
     'Test Topics': list(temp_test.values()),
     'Predicted test topics': list(temp_predicted.values())
    })

Predicted test topics                                        Test Topics  \
0                   [earn]                                             [earn]   
1                  [grain]                                            [grain]   
2                   [earn]                                             [earn]   
3                    [acq]                                              [acq]   
4                  [grain]                                            [grain]   
5                    [acq]                                              [acq]   
6                   [earn]                                             [earn]   
7               [money-fx]                                         [money-fx]   
8                  [trade]                                            [trade]   
9                   [earn]                                             [earn]   
10                  [earn]                                             [earn]   
11                  [earn]                                             [earn]   
12                 [crude]                                       [iron-steel]   
13                  [earn]                                             [earn]   
14                 [grain]                                        [meal-feed]   
15              [money-fx]                                              [lei]   
16                 [grain]                                            [grain]   
17                   [acq]                                              [acq]   
18                   [acq]                                              [acq]   
19                  [earn]                                             [earn]   
20              [money-fx]                                              [cpi]   
21                  [earn]                                             [earn]   
22                  [earn]                                             [earn]   
23                  [earn]                                             [earn]   
24                   [acq]                                             [ship]   
25                  [earn]                                             [earn]   
26                   [acq]                                              [acq]   
27                  [earn]  [acq, gnp, dlr, crude, wheat, cpi, oilseed, or...   
28              [money-fx]                                              [gnp]   
29                  [earn]                                              [ipi]   
...                    ...                                                ...   
2038                 [acq]                                              [acq]   
2039               [crude]                                            [crude]   
2040                [earn]                                             [earn]   
2041                [earn]                                             [earn]   
2042               [trade]                                            [trade]   
2043               [crude]                                            [crude]   
2044            [money-fx]                                         [money-fx]   
2045                 [acq]                                              [acq]   
2046            [money-fx]                                         [interest]   
2047                 [acq]                                              [acq]   
2048                [earn]                                             [earn]   
2049                [earn]                                             [earn]   
2050                [earn]                                             [earn]   
2051                [jobs]                                             [jobs]   
2052                 [acq]                                              [acq]   
2053                [earn]                                             [earn]   
2054                [earn]                                             [earn]   
2055                [earn]          

# Note: For example, in the row corresponding to row 27 in the above data frame  'earn' in the predicted column imply that each of the topic in the topics columns for the corresponding article are predicted as 'earn'.

In [20]:
end=time.time()
print("Time taken: ",end-start, "seconds")

Time taken:  623.3920772075653 seconds


In [21]:
start=time.time()

# Implementing with  test_size = 0.4 that is 40% of the corpus is taken as test

In [22]:
corpus_train,corpus_test,topics_train,topics_test = train_test_split(
        corpus, topics, test_size=0.4, random_state=42
    )

In [23]:
pipeline_bayes = Pipeline([
                ('tfidf', TfidfVectorizer(tokenizer=tokenize, min_df=3,
                        max_df=0.90, max_features=3000,
                        use_idf=True, sublinear_tf=True,
                        norm='l2')),
                ('clf',OneVsRestClassifier(MultinomialNB(
                    fit_prior=True, class_prior=None))),
            ])
pipeline_bayes.fit(corpus_train,topics_train)

predicted_topics= pipeline_bayes.predict(corpus_test)

from sklearn.metrics import precision_recall_fscore_support, accuracy_score

accuracy = accuracy_score(topics_test, predicted_topics)
precision, recall, f1_score, _ = precision_recall_fscore_support(topics_test, predicted_topics, average='weighted')

print("Accuracy: ", accuracy)
print("Precision: ", precision)
print("Recall: ", recall)
print("F1 score: ", f1_score)

Accuracy:  0.7248735429953815
Precision:  0.690626017087693
Recall:  0.7248735429953815
F1 score:  0.6697699066626455


In [24]:
cv_score_naive_bayes = cross_val_score(pipeline_bayes, corpus_train, topics_train, cv=5)
print("The cross validation score for Naive Bayes is:")
print(cv_score_naive_bayes)

The cross validation score for Naive Bayes is:
[0.67834167 0.68627451 0.69801616 0.70653789 0.72326103]


In [25]:
sklearn.metrics.confusion_matrix(topics_test,predicted_topics, labels=None, sample_weight=None)

array([[864,   0,   0, ...,   0,   0,   0],
       [ 10,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0],
       ...,
       [  0,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0],
       [  3,   0,   0, ...,   0,   0,   0]])

In [26]:
temp_test={}
temp_predicted={}
for i in range(0,len(corpus_test)):
    if corpus_test[i] in temp_test.keys():
        temp_test[corpus_test[i]].append(topics_test[i])
        temp_predicted[corpus_test[i]].append(predicted_topics[i])
    else:
        temp_test[corpus_test[i]]=[]
        temp_test[corpus_test[i]].append(topics_test[i])
        temp_predicted[corpus_test[i]]=[]
        temp_predicted[corpus_test[i]].append(predicted_topics[i])

for i in temp_test.keys():
    temp_test[i]=list(set(temp_test[i]))
    temp_predicted[i]=list(set(temp_predicted[i]))

pd.DataFrame(
    {'Test docs': list(temp_test.keys()),
     'Test Topics': list(temp_test.values()),
     'Predicted test topics': list(temp_predicted.values())
    })

Predicted test topics                                        Test Topics  \
0                   [earn]                                             [earn]   
1                  [grain]                                            [grain]   
2                   [earn]                                             [earn]   
3                    [acq]                                              [acq]   
4                  [grain]                                            [grain]   
5                    [acq]                                              [acq]   
6                   [earn]                                             [earn]   
7               [money-fx]                                         [money-fx]   
8                  [trade]                                            [trade]   
9                   [earn]                                             [earn]   
10                  [earn]                                             [earn]   
11                  [earn]                                             [earn]   
12                 [crude]                                       [iron-steel]   
13                  [earn]                                             [earn]   
14                 [grain]                                        [meal-feed]   
15              [money-fx]                                              [lei]   
16                 [grain]                                            [grain]   
17                   [acq]                                              [acq]   
18                   [acq]                                              [acq]   
19                  [earn]                                             [earn]   
20              [money-fx]                                              [cpi]   
21                  [earn]                                             [earn]   
22                  [earn]                                             [earn]   
23                  [earn]                                             [earn]   
24                   [acq]                                             [ship]   
25                  [earn]                                             [earn]   
26                   [acq]                                              [acq]   
27                  [earn]  [retail, acq, gnp, dlr, crude, wheat, cpi, oil...   
28              [money-fx]                                              [gnp]   
29                  [earn]                                              [ipi]   
...                    ...                                                ...   
4111                 [acq]                                              [acq]   
4112                [earn]                                             [earn]   
4113                 [acq]                                              [acq]   
4114                [earn]                                              [acq]   
4115            [interest]                                         [interest]   
4116                 [acq]                                              [acq]   
4117                 [acq]                                              [acq]   
4118                 [acq]                                              [acq]   
4119                [earn]                                              [bop]   
4120               [grain]                                            [sugar]   
4121               [trade]                                           [copper]   
4122                 [acq]                                              [acq]   
4123                [earn]                                             [earn]   
4124                [ship]                                             [ship]   
4125            [money-fx]                                         [money-fx]   
4126                 [acq]                                        [meal-feed]   
4127                [earn]                                             [earn]   
4128                 [acq]          

In [27]:
end=time.time()
print("Time taken: ",end-start, "seconds")

Time taken:  455.6999111175537 seconds


In [28]:
start=time.time()

# Implementing with  test_size = 0.1 that is 10% of the corpus is taken as test

In [29]:
corpus_train,corpus_test,topics_train,topics_test = train_test_split(
        corpus, topics, test_size=0.1, random_state=42
    )

In [30]:
pipeline_bayes = Pipeline([
                ('tfidf', TfidfVectorizer(tokenizer=tokenize, min_df=3,
                        max_df=0.90, max_features=3000,
                        use_idf=True, sublinear_tf=True,
                        norm='l2')),
                ('clf',OneVsRestClassifier(MultinomialNB(
                    fit_prior=True, class_prior=None))),
            ])
pipeline_bayes.fit(corpus_train,topics_train)



predicted_topics= pipeline_bayes.predict(corpus_test)

from sklearn.metrics import precision_recall_fscore_support, accuracy_score

accuracy = accuracy_score(topics_test, predicted_topics)
precision, recall, f1_score, _ = precision_recall_fscore_support(topics_test, predicted_topics, average='weighted')

print("Accuracy: ", accuracy)
print("Precision: ", precision)
print("Recall: ", recall)
print("F1 score: ", f1_score)

Accuracy:  0.7475813544415127
Precision:  0.7148719105156288
Recall:  0.7475813544415127
F1 score:  0.6963127102059349


In [31]:
cv_score_naive_bayes = cross_val_score(pipeline_bayes, corpus_train, topics_train, cv=5)
print("The cross validation score for Naive Bayes is:")
print(cv_score_naive_bayes)

The cross validation score for Naive Bayes is:
[0.71744354 0.7131068  0.71421569 0.72405312 0.72519841]


In [32]:
sklearn.metrics.confusion_matrix(topics_test,predicted_topics, labels=None, sample_weight=None)

array([[227,   0,   0, ...,   0,   0,   0],
       [  6,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0],
       ...,
       [  0,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0],
       [  0,   0,   0, ...,   0,   0,   0]])

In [33]:
temp_test={}
temp_predicted={}
for i in range(0,len(corpus_test)):
    if corpus_test[i] in temp_test.keys():
        temp_test[corpus_test[i]].append(topics_test[i])
        temp_predicted[corpus_test[i]].append(predicted_topics[i])
    else:
        temp_test[corpus_test[i]]=[]
        temp_test[corpus_test[i]].append(topics_test[i])
        temp_predicted[corpus_test[i]]=[]
        temp_predicted[corpus_test[i]].append(predicted_topics[i])

for i in temp_test.keys():
    temp_test[i]=list(set(temp_test[i]))
    temp_predicted[i]=list(set(temp_predicted[i]))

pd.DataFrame(
    {'Test docs': list(temp_test.keys()),
     'Test Topics': list(temp_test.values()),
     'Predicted test topics': list(temp_predicted.values())
    })

Predicted test topics                                        Test Topics  \
0                   [earn]                                             [earn]   
1                  [grain]                                            [grain]   
2                   [earn]                                             [earn]   
3                    [acq]                                              [acq]   
4                  [grain]                                            [grain]   
5                    [acq]                                              [acq]   
6                   [earn]                                             [earn]   
7               [money-fx]                                         [money-fx]   
8                  [trade]                                            [trade]   
9                   [earn]                                             [earn]   
10                  [earn]                                             [earn]   
11                  [earn]                                             [earn]   
12                 [crude]                                       [iron-steel]   
13                  [earn]                                             [earn]   
14                 [grain]                                        [meal-feed]   
15              [money-fx]                                              [lei]   
16                 [grain]                                            [grain]   
17                   [acq]                                              [acq]   
18                   [acq]                                              [acq]   
19                  [earn]                                             [earn]   
20              [money-fx]                                              [cpi]   
21                  [earn]                                             [earn]   
22                  [earn]                                             [earn]   
23                  [earn]                                             [earn]   
24                   [acq]                                             [ship]   
25                  [earn]                                             [earn]   
26                   [acq]                                              [acq]   
27                  [earn]  [acq, gnp, crude, wheat, cpi, orange, money-fx...   
28              [money-fx]                                              [gnp]   
29                  [earn]                                              [ipi]   
...                    ...                                                ...   
1018                [earn]                                             [earn]   
1019               [trade]                                            [trade]   
1020                 [acq]                                              [acq]   
1021                 [acq]                                            [crude]   
1022                [earn]                                             [earn]   
1023               [crude]                                          [propane]   
1024                 [acq]                                              [acq]   
1025                [earn]                                           [coffee]   
1026                [earn]                                             [earn]   
1027                 [acq]                                           [rubber]   
1028               [grain]                                            [grain]   
1029                [earn]                                             [earn]   
1030            [money-fx]                                              [gnp]   
1031                 [acq]                                         [pet-chem]   
1032                [earn]                                             [earn]   
1033               [grain]                                            [grain]   
1034                [earn]                                           [coffee]   
1035                [earn]          

In [34]:
end=time.time()
print("Time taken: ",end-start, "seconds")

Time taken:  638.039274930954 seconds
